In [1]:
""" mount drive """

import os

GOOGLE_DIR = '/content/drive/My Drive/DL_Project'
LOCAL_DIR = '/home/ziyan/Desktop/Deep Learning Project'

def colab_mount_google_drive():
    drive.mount('/content/drive', force_remount=True)
    os.chdir(GOOGLE_DIR)
    os.listdir()

def mount_local_drive():
    os.chdir(LOCAL_DIR)
    os.listdir()

try:
    from google.colab import drive
    colab_mount_google_drive()
    DIR = GOOGLE_DIR
    print('Mounted google drive')
except ModuleNotFoundError:
    mount_local_drive
    DIR = LOCAL_DIR
    print('Mounted local drive')

Mounted local drive


In [2]:
import pandas as pd
df1 = pd.read_csv('input_df_cross_assets_v2/input_20181101.csv.gz')
# df1.info()
df1['mid_lag_30s'].iloc[3565:3580]
# df1.head()

3565   -0.7
3566   -0.6
3567   -0.6
3568   -0.6
3569   -0.7
3570   -0.4
3571   -0.6
3572   -0.5
3573   -0.4
3574   -0.5
3575   -0.5
3576   -0.5
3577   -0.5
3578   -0.5
3579   -0.6
Name: mid_lag_30s, dtype: float64

In [2]:
""" model specification """

# for dataset
product = 'input_df_cross_assets_v2'
fields = [
    'mid_lag_10s', 'mid_lag_30s', 'mid_lag_01m',
    'wmid_ma_05m', 'wmid_ma_10m', 
    'wmid_max_05m', 'wmid_max_10m', 
    'wmid_min_05m', 'wmid_min_10m', 
    'wmid_bidask_01m',
    'total_volume_10s', 'total_volume_01m', 
    'signed_volume_10s', 'signed_volume_10s',
    'signed_tick_10s', 'signed_tick_01m',
    'IF_mid_lag_05s', 'IF_mid_lag_30s',
    'IF_total_volume_10s', 'IF_total_volume_01m',
    'IC_mid_lag_05s', 'IC_mid_lag_30s',
    'IC_total_volume_10s', 'IC_total_volume_01m'
]  # column names
y_field = 'mid_lag_30s'

series_length = 60  # number of samples
sample_interval = 30  # sample every 30 seconds
cache_limit = 300

use_cuda = True

# for train and validate dataloader
params = {
    'batch_size': 1,
    'shuffle': False,
    'num_workers': 3
}

train_sd = '20180102'
train_ed = '20180930'
validate_sd = '20181001'
validate_ed = '20181031'
test_sd = '20181101'
test_ed = '20181231'

In [4]:
""" create index table for selected product """
import re

os.chdir(os.path.join(DIR, product))
table_file = f'{product}_train_indexes_{series_length}_{sample_interval}.csv'

if not os.path.isfile(table_file):  # skip this step if the index tables already exists (only check train here)
    files = {'train': [], 'validate': [], 'test': []}  # dict of list of dicts
    
    for fn in sorted(os.listdir()):
        # rows number is first subtracted by {series_length} at the begining
        m = re.search('input_(2018\d{4})', fn)
        if m:
            date = m.group(1)
            if date <= train_ed:
                data_type = 'train'
            elif date <= validate_ed:
                data_type = 'validate'
            else:
                data_type = 'test'
            
            df = pd.read_csv(fn)
            cutoff = series_length * sample_interval / 0.5  # drop the tailing indexes
            files[data_type].append({'file_name': fn, 'rows': int(df.shape[0] - cutoff - 1)})

    for data_type in files:
        table = pd.DataFrame(files[data_type])
        table['date'] = table['file_name'].str.split('_').str[-1].str.split('.').str[0]
        table_file = f'{product}_{data_type}_indexes_{series_length}_{sample_interval}.csv'
        table.to_csv(f'{table_file}', index=False)
        print(f'Wrote {data_type} index table to {product}/{table_file}')
else:
    print('Skipped.')

os.chdir(os.path.join(DIR))

Skipped.


In [3]:
""" Create data generators """

from torch.utils import data
from dataset import Dataset

# create a train, validation and test data loader
train_set = Dataset(train_sd, train_ed, product=product, data_type='train', x_fields=fields, y_field=y_field, 
                    series_length=series_length, sample_interval=sample_interval,
                    cache_limit=cache_limit, use_cuda=use_cuda)
train_loader = data.DataLoader(train_set, **params)

validation_set = Dataset(validate_sd, validate_ed, product=product, data_type='validate', x_fields=fields, y_field=y_field,
                         series_length=series_length, sample_interval=sample_interval,
                         cache_limit=cache_limit, use_cuda=use_cuda)
validation_loader = data.DataLoader(validation_set, **params)

test_set = Dataset(test_sd, test_ed, product=product, data_type='test', x_fields=fields, y_field=y_field,
                   series_length=series_length, sample_interval=sample_interval,
                   cache_limit=cache_limit, use_cuda=use_cuda)
# for test only
test_params = {
    'batch_size': 1,
    'shuffle': False,
    'num_workers': 3
}
test_loader = data.DataLoader(test_set, **test_params)

In [6]:
""" 
Init and train model

Main issues:
1. tensor shape for LSTM (3 dimensions with batch as the middle one)
2. model (parameter) and data precision should match by using float()
"""

import gc
import torch.optim as optim
from time import time
from models import *

if use_cuda:
    model = PrototypeModel(input_size=len(fields), num_layers=series_length).float().cuda()  # use float precision instead of double
else:
    model = PrototypeModel(input_size=len(fields), num_layers=series_length).float()

criterion = nn.SmoothL1Loss()

optimizer = optim.SGD(model.parameters(), lr=0.01, momentum=0.6)
model.train()
epoch_error = {}
out = []

for epoch in range(1):
    running_loss = 0.0
    start_time = time()
    epoch_error[epoch] = []
    batch_idx = 0
    
    for data, target in train_loader:
        batch_idx += 1
        optimizer.zero_grad()
#         print(data)
        if use_cuda:
            prediction = model(data.float().cuda())
        else:
            prediction = model(data.float())
        
        if use_cuda:
            loss = criterion(prediction, target.cuda())
        else:
            loss = criterion(prediction, target)
        
        loss.backward()
        optimizer.step()
        
        # print statistics
        running_loss += loss.item()
        cost_time = time() - start_time
#         print(prediction, target)
        print('[epoch: %d, batch:  %5d] target: %6.2f | pred: %6.2f | loss: %.5f  | %.2f' %
              (epoch + 1, batch_idx + 1, target, prediction, running_loss, cost_time))
        
        out.append([float(target), float(prediction)])
        running_loss = 0.0
        start_time = time()
        
        epoch_error[epoch].append(loss)
        
        # Remove this when actually training. 
        # Used to terminate early. 
        if batch_idx > 50000: 
            break
            
#     gc.collect()  # does it help?

/home/ziyan/.local/lib/python3.7/site-packages/torch/nn/modules/loss.py:782: UserWarning: Using a target size (torch.Size([1])) that is different to the input size (torch.Size([])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.smooth_l1_loss(input, target, reduction=self.reduction)


[epoch: 1, batch:      2] target:   0.20 | pred:   0.10 | loss: 0.00545  | 0.37
[epoch: 1, batch:      3] target:   0.20 | pred:   0.10 | loss: 0.00464  | 0.00
[epoch: 1, batch:      4] target:   0.20 | pred:   0.13 | loss: 0.00212  | 0.00
[epoch: 1, batch:      5] target:   0.20 | pred:   0.14 | loss: 0.00171  | 0.00
[epoch: 1, batch:      6] target:   0.20 | pred:   0.15 | loss: 0.00143  | 0.00
[epoch: 1, batch:      7] target:   0.20 | pred:   0.15 | loss: 0.00127  | 0.00
[epoch: 1, batch:      8] target:   0.20 | pred:   0.15 | loss: 0.00112  | 0.00
[epoch: 1, batch:      9] target:   1.10 | pred:   0.16 | loss: 0.44450  | 0.00
[epoch: 1, batch:     10] target:   1.10 | pred:   0.19 | loss: 0.41458  | 0.00
[epoch: 1, batch:     11] target:   1.10 | pred:   0.22 | loss: 0.38341  | 0.00
[epoch: 1, batch:     12] target:   1.10 | pred:   0.27 | loss: 0.34505  | 0.00
[epoch: 1, batch:     13] target:   1.10 | pred:   0.33 | loss: 0.29584  | 0.00
[epoch: 1, batch:     14] target:   1.40

[epoch: 1, batch:    109] target:  -1.00 | pred:  -1.32 | loss: 0.05259  | 0.00
[epoch: 1, batch:    110] target:  -1.00 | pred:  -1.29 | loss: 0.04093  | 0.00
[epoch: 1, batch:    111] target:  -1.90 | pred:  -1.24 | loss: 0.21492  | 0.00
[epoch: 1, batch:    112] target:  -2.00 | pred:  -1.26 | loss: 0.27299  | 0.00
[epoch: 1, batch:    113] target:  -1.90 | pred:  -1.32 | loss: 0.16941  | 0.00
[epoch: 1, batch:    114] target:  -1.90 | pred:  -1.39 | loss: 0.13186  | 0.00
[epoch: 1, batch:    115] target:  -1.90 | pred:  -1.46 | loss: 0.09624  | 0.00
[epoch: 1, batch:    116] target:  -1.80 | pred:  -1.54 | loss: 0.03469  | 0.00
[epoch: 1, batch:    117] target:  -1.70 | pred:  -1.60 | loss: 0.00477  | 0.00
[epoch: 1, batch:    118] target:  -1.70 | pred:  -1.65 | loss: 0.00124  | 0.00
[epoch: 1, batch:    119] target:  -1.70 | pred:  -1.68 | loss: 0.00013  | 0.00
[epoch: 1, batch:    120] target:  -1.60 | pred:  -1.71 | loss: 0.00560  | 0.00
[epoch: 1, batch:    121] target:  -1.60

[epoch: 1, batch:    215] target:  -0.00 | pred:  -0.14 | loss: 0.00944  | 0.00
[epoch: 1, batch:    216] target:  -0.10 | pred:  -0.14 | loss: 0.00067  | 0.00
[epoch: 1, batch:    217] target:  -0.10 | pred:  -0.14 | loss: 0.00065  | 0.00
[epoch: 1, batch:    218] target:  -0.10 | pred:  -0.14 | loss: 0.00062  | 0.00
[epoch: 1, batch:    219] target:  -0.10 | pred:  -0.13 | loss: 0.00056  | 0.00
[epoch: 1, batch:    220] target:  -0.10 | pred:  -0.13 | loss: 0.00050  | 0.00
[epoch: 1, batch:    221] target:  -0.00 | pred:  -0.13 | loss: 0.00828  | 0.00
[epoch: 1, batch:    222] target:  -0.00 | pred:  -0.12 | loss: 0.00676  | 0.00
[epoch: 1, batch:    223] target:  -0.00 | pred:  -0.11 | loss: 0.00628  | 0.00
[epoch: 1, batch:    224] target:   0.10 | pred:  -0.11 | loss: 0.02151  | 0.00
[epoch: 1, batch:    225] target:   0.20 | pred:  -0.09 | loss: 0.04256  | 0.00
[epoch: 1, batch:    226] target:   0.20 | pred:  -0.07 | loss: 0.03762  | 0.00
[epoch: 1, batch:    227] target:   0.20

[epoch: 1, batch:    321] target:  -3.10 | pred:  -3.14 | loss: 0.00085  | 0.00
[epoch: 1, batch:    322] target:  -3.10 | pred:  -3.15 | loss: 0.00136  | 0.00
[epoch: 1, batch:    323] target:  -3.10 | pred:  -3.13 | loss: 0.00054  | 0.00
[epoch: 1, batch:    324] target:  -2.90 | pred:  -3.10 | loss: 0.02082  | 0.00
[epoch: 1, batch:    325] target:  -2.80 | pred:  -3.08 | loss: 0.03921  | 0.00
[epoch: 1, batch:    326] target:  -2.70 | pred:  -2.97 | loss: 0.03682  | 0.00
[epoch: 1, batch:    327] target:  -2.70 | pred:  -2.84 | loss: 0.01009  | 0.00
[epoch: 1, batch:    328] target:  -1.40 | pred:  -2.76 | loss: 0.85820  | 0.00
[epoch: 1, batch:    329] target:  -2.00 | pred:  -2.35 | loss: 0.05956  | 0.00
[epoch: 1, batch:    330] target:  -1.10 | pred:  -1.95 | loss: 0.36214  | 0.00
[epoch: 1, batch:    331] target:  -1.70 | pred:  -1.68 | loss: 0.00012  | 0.00
[epoch: 1, batch:    332] target:  -1.60 | pred:  -1.52 | loss: 0.00328  | 0.00
[epoch: 1, batch:    333] target:  -1.60

...

[epoch: 1, batch:  49549] target:   0.00 | pred:  -0.46 | loss: 0.10633  | 0.00
[epoch: 1, batch:  49550] target:   0.10 | pred:  -0.42 | loss: 0.13761  | 0.00
[epoch: 1, batch:  49551] target:   0.20 | pred:  -0.38 | loss: 0.16887  | 0.00
[epoch: 1, batch:  49552] target:   0.20 | pred:  -0.37 | loss: 0.16085  | 0.00
[epoch: 1, batch:  49553] target:   0.00 | pred:  -0.33 | loss: 0.05346  | 0.00
[epoch: 1, batch:  49554] target:   0.10 | pred:  -0.30 | loss: 0.07902  | 0.00
[epoch: 1, batch:  49555] target:   0.20 | pred:  -0.27 | loss: 0.10927  | 0.00
[epoch: 1, batch:  49556] target:   0.50 | pred:  -0.24 | loss: 0.27511  | 0.00
[epoch: 1, batch:  49557] target:   0.40 | pred:  -0.21 | loss: 0.18516  | 0.00
[epoch: 1, batch:  49558] target:   0.40 | pred:  -0.17 | loss: 0.16463  | 0.00
[epoch: 1, batch:  49559] target:   0.20 | pred:  -0.14 | loss: 0.05742  | 0.00
[epoch: 1, batch:  49560] target:   0.30 | pred:  -0.11 | loss: 0.08406  | 0.00
[epoch: 1, batch:  49561] target:   0.30

[epoch: 1, batch:  49656] target:   1.00 | pred:   1.02 | loss: 0.00017  | 0.00
[epoch: 1, batch:  49657] target:   1.00 | pred:   1.03 | loss: 0.00048  | 0.00
[epoch: 1, batch:  49658] target:   1.00 | pred:   1.03 | loss: 0.00060  | 0.00
[epoch: 1, batch:  49659] target:   1.00 | pred:   1.03 | loss: 0.00060  | 0.00
[epoch: 1, batch:  49660] target:   1.00 | pred:   1.03 | loss: 0.00046  | 0.00
[epoch: 1, batch:  49661] target:  -0.10 | pred:   1.03 | loss: 0.62809  | 0.00
[epoch: 1, batch:  49662] target:   0.50 | pred:   0.97 | loss: 0.11049  | 0.00
[epoch: 1, batch:  49663] target:   0.50 | pred:   0.90 | loss: 0.08110  | 0.01
[epoch: 1, batch:  49664] target:   0.60 | pred:   0.84 | loss: 0.02869  | 0.00
[epoch: 1, batch:  49665] target:   0.60 | pred:   0.79 | loss: 0.01801  | 0.00
[epoch: 1, batch:  49666] target:   0.60 | pred:   0.75 | loss: 0.01118  | 0.00
[epoch: 1, batch:  49667] target:   0.50 | pred:   0.72 | loss: 0.02487  | 0.00
[epoch: 1, batch:  49668] target:   0.40

[epoch: 1, batch:  49760] target:  -0.10 | pred:  -0.13 | loss: 0.00042  | 0.00
[epoch: 1, batch:  49761] target:  -0.20 | pred:  -0.13 | loss: 0.00254  | 0.00
[epoch: 1, batch:  49762] target:  -0.10 | pred:  -0.13 | loss: 0.00048  | 0.00
[epoch: 1, batch:  49763] target:  -0.10 | pred:  -0.13 | loss: 0.00051  | 0.00
[epoch: 1, batch:  49764] target:  -0.10 | pred:  -0.13 | loss: 0.00053  | 0.00
[epoch: 1, batch:  49765] target:  -0.30 | pred:  -0.12 | loss: 0.01575  | 0.00
[epoch: 1, batch:  49766] target:  -0.30 | pred:  -0.12 | loss: 0.01598  | 0.00
[epoch: 1, batch:  49767] target:  -0.30 | pred:  -0.13 | loss: 0.01475  | 0.00
[epoch: 1, batch:  49768] target:  -0.30 | pred:  -0.14 | loss: 0.01318  | 0.00
[epoch: 1, batch:  49769] target:  -0.30 | pred:  -0.15 | loss: 0.01165  | 0.00
[epoch: 1, batch:  49770] target:  -0.30 | pred:  -0.15 | loss: 0.01082  | 0.00
[epoch: 1, batch:  49771] target:  -0.30 | pred:  -0.16 | loss: 0.01011  | 0.00
[epoch: 1, batch:  49772] target:  -0.30

[epoch: 1, batch:  49867] target:   0.20 | pred:   0.40 | loss: 0.01910  | 0.00
[epoch: 1, batch:  49868] target:   0.20 | pred:   0.38 | loss: 0.01575  | 0.00
[epoch: 1, batch:  49869] target:   0.30 | pred:   0.36 | loss: 0.00194  | 0.00
[epoch: 1, batch:  49870] target:   0.10 | pred:   0.31 | loss: 0.02232  | 0.00
[epoch: 1, batch:  49871] target:   0.30 | pred:   0.30 | loss: 0.00001  | 0.00
[epoch: 1, batch:  49872] target:   0.40 | pred:   0.30 | loss: 0.00460  | 0.00
[epoch: 1, batch:  49873] target:   0.10 | pred:   0.31 | loss: 0.02156  | 0.00
[epoch: 1, batch:  49874] target:   0.20 | pred:   0.30 | loss: 0.00513  | 0.00
[epoch: 1, batch:  49875] target:   0.40 | pred:   0.30 | loss: 0.00537  | 0.00
[epoch: 1, batch:  49876] target:   0.30 | pred:   0.30 | loss: 0.00000  | 0.00
[epoch: 1, batch:  49877] target:   0.30 | pred:   0.29 | loss: 0.00002  | 0.00
[epoch: 1, batch:  49878] target:   0.30 | pred:   0.30 | loss: 0.00001  | 0.00
[epoch: 1, batch:  49879] target:   0.30

[epoch: 1, batch:  49975] target:   0.20 | pred:   0.57 | loss: 0.06754  | 0.00
[epoch: 1, batch:  49976] target:   0.10 | pred:   0.57 | loss: 0.10874  | 0.00
[epoch: 1, batch:  49977] target:   0.70 | pred:   0.55 | loss: 0.01170  | 0.00
[epoch: 1, batch:  49978] target:   0.30 | pred:   0.54 | loss: 0.02920  | 0.00
[epoch: 1, batch:  49979] target:   0.20 | pred:   0.53 | loss: 0.05403  | 0.00
[epoch: 1, batch:  49980] target:   0.20 | pred:   0.51 | loss: 0.04757  | 0.00
[epoch: 1, batch:  49981] target:   0.30 | pred:   0.49 | loss: 0.01754  | 0.00
[epoch: 1, batch:  49982] target:   0.60 | pred:   0.47 | loss: 0.00880  | 0.00
[epoch: 1, batch:  49983] target:   0.40 | pred:   0.46 | loss: 0.00177  | 0.00
[epoch: 1, batch:  49984] target:  -0.70 | pred:   0.46 | loss: 0.65528  | 0.00
[epoch: 1, batch:  49985] target:   0.20 | pred:   0.42 | loss: 0.02460  | 0.00
[epoch: 1, batch:  49986] target:   0.30 | pred:   0.39 | loss: 0.00439  | 0.00
[epoch: 1, batch:  49987] target:  -0.30

In [7]:
# """Local Evaluation / Test"""

# import numpy as np

# test_mode = False

# model.eval()
# out = []
# # model.cuda()
# loader = validation_loader if not test_mode else test_loader

# with torch.no_grad():
#     mse = []
#     batch_idx = 0
    
#     for data, target in loader:
#         batch_idx += 1
# #         print(data, target)
#         prediction = model(data.float().cuda())
#         mse.append(np.square(prediction.cpu() - target))
#         if test_mode:
#             out.append([float(target), float(prediction)])
        
#         if test_mode:
#             print('[epoch: %d, batch:  %5d] target: %6.2f | pred: %6.2f' %
#                   (epoch + 1, batch_idx + 1, target, prediction))
#         # Used to terminate early, remove.
#         if batch_idx >= 1000: 
#             break

# print('MSE: %.2f' % (np.array(mse).mean()))
# if test_mode:
#     print(out)

In [8]:
for name, param in model.named_parameters():
    if param.requires_grad:
        print(name, param.data)

lstm.weight_ih_l0 tensor([[-0.1583, -0.1503, -0.0111,  ...,  0.0805,  0.0488, -0.0084],
        [ 0.0573,  0.0821, -0.0662,  ..., -0.0387, -0.0129,  0.1691],
        [ 0.0752, -0.0885,  0.1761,  ...,  0.1391, -0.1266,  0.1107],
        ...,
        [ 0.0996,  0.0892,  0.1252,  ...,  0.0787, -0.0075,  0.1367],
        [ 0.0003, -0.0765,  0.0813,  ..., -0.0175, -0.0460, -0.0536],
        [ 0.1451,  0.2050,  0.1978,  ...,  0.1735,  0.1761,  0.1264]],
       device='cuda:0')
lstm.weight_hh_l0 tensor([[-0.1738,  0.0196,  0.0447,  ..., -0.1102, -0.0953, -0.0794],
        [ 0.0997, -0.0940, -0.1387,  ..., -0.0073, -0.0131, -0.0689],
        [ 0.1318,  0.0193, -0.1007,  ..., -0.0878, -0.0080,  0.1089],
        ...,
        [ 0.0468,  0.1686, -0.1732,  ...,  0.1710,  0.0613,  0.0818],
        [ 0.1546, -0.0297, -0.0291,  ...,  0.0996,  0.0329,  0.0204],
        [-0.0215,  0.0940,  0.0773,  ...,  0.0502,  0.1071, -0.0267]],
       device='cuda:0')
lstm.bias_ih_l0 tensor([-0.0968,  0.0515, -0.103

In [10]:
with open('test result_2.csv', 'w') as f:
    for lst in out:
        f.write(','.join([str(i) for i in lst])+'\n')
        

In [14]:
import torch.optim as optim
from time import time
from models import *
model = LinearRegressionModel(len(fields)).cuda()
criterion = torch.nn.MSELoss(size_average = False) 
optimizer = torch.optim.SGD(our_model.parameters(), lr = 0.01)
batch_idx=0
out=[]
for data, target in train_loader:
        batch_idx += 1
        optimizer.zero_grad()
#         print(data)
        if use_cuda:
            prediction = model(data[-1].float().cuda())
        else:
            prediction = model(data[-1].float())
        
        if use_cuda:
            loss = criterion(prediction, target.cuda())
        else:
            loss = criterion(prediction, target)
        
        loss.backward()
        optimizer.step()
        
        print('[epoch: %d, batch:  %5d] target: %6.2f | pred: %6.2f | loss: %.5f ' %
              (1, batch_idx + 1, target, prediction, loss))
        
        out.append([float(target), float(prediction)])
        
        # Remove this when actually training. 
        # Used to terminate early. 
        if batch_idx > 50000: 
            break

/home/ziyan/.local/lib/python3.7/site-packages/torch/nn/_reduction.py:43: UserWarning: size_average and reduce args will be deprecated, please use reduction='sum' instead.
  warnings.warn(warning.format(ret))
/home/ziyan/.local/lib/python3.7/site-packages/torch/nn/modules/loss.py:431: UserWarning: Using a target size (torch.Size([1])) that is different to the input size (torch.Size([60, 1, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


ValueError: only one element tensors can be converted to Python scalars

In [16]:
import importlib
importlib.reload(models)
from models import LinearRegressionModel

ImportError: cannot import name 'LinearRegressionModel' from 'models' (/home/ziyan/Desktop/Deep Learning Project/models.py)